In [2]:
import numpy as np
np.set_printoptions(suppress=True, precision=5)
import pandas as pd
import scipy.spatial.distance as spdist
from IPython.display import display
import time

import matplotlib.pyplot as plt
from PIL import Image

# for performance measurement
# %lprun -f [function to profile] [execution trigger]
# %load_ext line_profiler

In [3]:
query_scores = np.fromfile("native-queries/native-query-scores.bin", dtype='f')
query_scores.shape

(6540000,)

In [4]:
print(query_scores[0:100])

[1.      0.86154 0.76303 0.70082 0.69154 0.63187 0.63078 0.597   0.39991
 0.39806 0.34944 0.3238  0.31499 0.2983  0.24113 0.23587 0.233   0.22473
 0.22309 0.21943 0.20288 0.19483 0.19241 0.18163 0.17281 0.17081 0.16959
 0.16804 0.16621 0.16207 0.16194 0.15713 0.15247 0.14817 0.1462  0.14411
 0.14166 0.13771 0.13493 0.13477 0.13264 0.13195 0.12906 0.12826 0.12664
 0.12257 0.12221 0.12177 0.11971 0.11966 0.11786 0.11386 0.11345 0.11311
 0.11298 0.1124  0.11113 0.10563 0.10419 0.10283 0.10262 0.10107 0.1008
 0.10015 0.09225 0.09151 0.08893 0.08851 0.08758 0.08668 0.0863  0.08616
 0.08545 0.08544 0.08505 0.08456 0.08343 0.08306 0.08281 0.08263 0.08257
 0.08188 0.08015 0.07971 0.07845 0.07843 0.07547 0.07515 0.07509 0.07455
 0.07315 0.07139 0.07137 0.07098 0.07012 0.06991 0.06914 0.06889 0.06855
 0.06825]


In [5]:
# reshape np array into 327 x 20000 array
query_scores = query_scores.reshape(327, 20000)

In [6]:
query_frame_ids = np.fromfile("native-queries/native-query-frame-IDs.bin", dtype='i')
query_frame_ids.shape

(6540000,)

In [7]:
print(query_frame_ids[0:100])

[ 5697  5645 18842 10847  4872 15282  5644 11257  3449  5380 15283     1
  4489 17026 10845   965  5643 18845 12903  2241 19246  2226 15342  3245
   964  8758 12083 10711 19007 14892 15213 16454  4493 16475  3725  7890
  4927   498 10710   452  8128 14617  2564   963 19121  2810 14099  3556
 13992  6988   980 18702  2454 14890 13953  2663 16117  8347  2453 14374
  9795  4375   729  5819  9391 12902 10846 15811  7889 16186 10848  3451
 17975 19951 18358 16476 18843 18686  6129  7380 12721  5267  9626 17687
 12334 15387 14540 14911  3622  4589 12085  7879 10496  3482 14615  6905
 10152 19706  3481  9759]


In [8]:
# reshape np array into 327 x 20000 array
query_frame_ids = query_frame_ids.reshape(327, 20000)

In [9]:
frame_features = np.fromfile("native-queries/frame-features.bin", dtype='f')
frame_features.shape

(2560000,)

In [10]:
print(frame_features[0:100])

[ 0.16691  0.56416  0.32702 -0.11217  0.19371  0.5717   0.1079  -0.04373
  0.22609  0.0775   0.14043  0.08696  0.04192 -0.00181  0.02947 -0.05099
 -0.02955 -0.00342  0.06661  0.03804  0.01074  0.07426  0.05218  0.01714
 -0.05492  0.04126 -0.06568  0.05996 -0.03729 -0.06075  0.03306 -0.02322
 -0.01536 -0.00883  0.00342  0.01878  0.04251  0.02456 -0.0076   0.01512
  0.02498 -0.02595 -0.01833 -0.00277 -0.00717  0.00178 -0.00322  0.00384
  0.00497  0.01047 -0.0292   0.01857  0.01496  0.01483  0.03119  0.02505
 -0.03294  0.02223 -0.0336   0.01726 -0.01783  0.00684  0.01794 -0.00201
 -0.0444  -0.01943 -0.01307 -0.00856 -0.00216  0.00839  0.00798  0.0165
  0.02071 -0.00376  0.01017  0.01088  0.00909 -0.0092  -0.00007 -0.03174
 -0.05065  0.03829  0.00424  0.00299  0.01122 -0.01765  0.00512 -0.00211
 -0.00814 -0.04114 -0.01271  0.01588 -0.01666  0.00565  0.01208 -0.02558
 -0.01413 -0.01899 -0.02829 -0.01703]


In [11]:
# reshape np array into 20000 x 128 array
frame_features = frame_features.reshape(20000, 128)

In [11]:
queries = pd.read_csv(r"C:\Users\KWP\bachelor_thesis\native-queries\native-queries.csv", sep=';', names=['frame_ID', 'query'])
queries.head()

frame_ID                                              query
0      498  A man wearing a black t-shirt and pants riding...
1    16554  An old black car riding in a desert with a few...
2    16683                logo,black circles and red pins,,,,
3     2629  defensive wall and bridge next to trees and gr...
4     6405  Hands wearing two rings holding a doll with pi...

In [29]:
# SOM Implementation
class SOM:
    
    def __init__(self, som_size, data, sigma, lambda_, learning_rate, iterations, query_scores=np.empty(shape=1), 
                 auto_var_adjustment=False, var_param=0):
        
        self.som_size = som_size
        # sigma - radius of a neighborhood
        self.sigma = sigma
        self.learning_rate = learning_rate
        # number of iterations
        self.iterations = iterations
        # lambda - time constant. used to update (= decay) the radius and learning rate
        self.lambda_ = lambda_
        
        # for reproduction purposes
        np.random.seed(241)
        # intialize SOM with random weights
        if auto_var_adjustment == True or var_param > 0:
            self.data = np.append(data, np.zeros((20000, 1)), axis=1)
            self.som = np.random.random((som_size, som_size, self.data.shape[1]))
        else: 
            self.data = data
            self.som = np.random.random((som_size, som_size, data.shape[1]))
        
        self.query_scores = query_scores
        
        # we can decide to adjust the variance of query_scores automatically, 
        # or specify the extent of amplification via hyperparameter 'variance_param'
         
        # auto_var_adjustment (false by default) automatically adjusts the variance of query_scores so that 
        # var(query_scores) = sum_over_features(var(feature)) (roughly) 
        
        if auto_var_adjustment == True and var_param == 0:
            
            self.adjust_var()
            self.initial_bias()
        
        if var_param > 0 and auto_var_adjustment == False:

            self.query_scores = self.query_scores * var_param
            self.initial_bias()
                   
    def initial_bias(self):

        # add query scores to SOM as another feature, considering the position of the nodes

        # we will divide query_scores into N intervals of equal size (where SOM has size n x n)
        # then from each interval corresponding to each row, pick N values randomly.

        # for example, for 5 x 5 SOM: divide query_score into 5 intervals
        # top 80~100% values, 60~80%, ..., 0~20%. Nodes in top row are assigned 5 random values from the first interval, and so on.

        cutpoints = []
        interval_size = 100 / self.som_size 
        for i in range(1, self.som_size):

            cutpoint = np.quantile(self.query_scores, interval_size * i * 0.01)
            cutpoints.append(cutpoint)

            if i == 1:

                bottom_interval = self.query_scores[self.query_scores < cutpoint]

                # assign to bottom nodes i.e. som[size-1, 0] ... som[size-1, size-1]
                for j in range(self.som_size):
                    self.som[self.som_size-1, j, 128] = np.random.choice(bottom_interval, size=1)[0]

            else:
                interval = self.query_scores[np.logical_and(self.query_scores > cutpoints[i-2], self.query_scores < cutpoint)]

                # assign to middle row nodes e.g. som[1, 0] ... som[1, size-1]
                for j in range(self.som_size):
                    self.som[self.som_size-i, j, 128] = np.random.choice(interval, size=1)[0]

                if i == self.som_size-1:

                    top_interval = self.query_scores[self.query_scores > cutpoint]         

                    # assign to top nodes i.e. som[0, 0] ... som[0, size-1]
                    for j in range(self.som_size):

                        self.som[0, j, 128] = np.random.choice(top_interval, size=1)[0]

    def adjust_var(self):
        # variance of randomly initialized SOM nodes (on original features)
        sum = 0
        for i in range(self.som_size):
            for j in range(self.som_size):
                sum += self.som[i, j].var()
        print("sum of variance over all SOM nodes' original features: {}".format(sum))
            
        # if the var difference is less than 0.1, then we adjust the query scores
        for i in range(200):
            tmp = query_scores * i
            if abs(sum - tmp.var()) < 0.05:
                print("variance of adjusted query scores: {}".format(tmp.var()))

                break
        self.query_scores = tmp
    
    def update_learning_rate(self, i):
        return self.learning_rate * np.exp(-i / self.lambda_)

    def update_sigma(self, i):
        return self.sigma * np.exp(-i / self.lambda_)

    # smart implementation?
    def neighborhood_function(self, sigma, dist):
        return np.exp(-(dist ** 2) / (2 * (sigma ** 2)))
    
    # improved euclidean distance function
    def euclidean_dist(self, x, y):
        return spdist.cdist(x.reshape(1, -1), y.reshape(1, -1), 'euclidean').reshape(1)[0]
    
    # finding Best Matching Unit (TODO later: consdier ranking)
    def find_bmu(self, vector):
        
        min_dist = 1e+10
        
        # since we added another feature to SOM, we cannot calculate the distance as before. 
        # we have to make sure the 129th columns of the vectors are identical
        if(self.som[0, 0].shape[0] == 129):
    
            for i in range(self.som.shape[0]):
                for j in range(self.som.shape[1]):
                    
                    vector[128] = self.som[i, j, 128]
                    
                    dist = self.euclidean_dist(self.som[i, j], vector)

                    if dist < min_dist:
                        min_dist = dist
                        bmu_index = np.array([i, j])

        # regular version
        else:
            for i in range(self.som.shape[0]):
                for j in range(self.som.shape[1]):

                    dist = self.euclidean_dist(self.som[i, j], vector)

                    if dist < min_dist:
                        min_dist = dist
                        bmu_index = np.array([i, j])

        return bmu_index
                    
    def train(self):
        
        start_time = time.time()
        
        # for reproduction purposes
        np.random.seed(319)
        index_list = np.random.permutation(20000)
        
        # again, because we added another column, we want to make sure the newly added column values match
        if(self.som[0, 0].shape[0] == 129):
            
            for random_index in index_list:

                for t in range(self.iterations):

                    random_input = self.data[random_index, :]

                    bmu_index = self.find_bmu(random_input)

                    # update learning rate and sigma with current time
                    learning_rate = self.update_learning_rate(t)
                    sigma = self.update_sigma(t) 

                    # update the weights of BMU and its neighborhood
                    for i in range(self.som.shape[0]):
                        for j in range(self.som.shape[1]):
                            
                            som_node = np.array([i,j])
                            dist = self.euclidean_dist(som_node, bmu_index)
                            
                            random_input[128] = self.som[i, j, 128]
                            self.som[i, j]=self.som[i,j]+learning_rate*self.neighborhood_function(sigma, dist)*(random_input-self.som[i,j])
    
        # regular version
        else:
            
            for random_index in index_list:

                for t in range(self.iterations):

                    random_input = self.data[random_index, :]
                    bmu_index = self.find_bmu(random_input)

                    # update learning rate and sigma with current time
                    learning_rate = self.update_learning_rate(t)
                    sigma = self.update_sigma(t) 

                    # update the weights of BMU and its neighborhood
                    for i in range(self.som.shape[0]):
                        for j in range(self.som.shape[1]):
                            som_node = np.array([i,j])
                            dist = self.euclidean_dist(som_node, bmu_index)
                            self.som[i, j]=self.som[i,j]+learning_rate*self.neighborhood_function(sigma, dist)*(random_input-self.som[i,j])
            
        print("Training complete. Time elapsed: %s seconds" % (time.time() - start_time))

    # putting the 3 functions below together
    def display_results(self):
        
        start_time = time.time()
        
        filepaths = pd.read_csv(r"C:\Users\KWP\bachelor_thesis\native-queries\frame-ID-to-filepath.csv", sep=' ', names=['filename', 'ID'])
        df = self.node2image(filepaths)
        images = self.select_images(df)
        self.display_images(images)
        
        print("Time elapsed: %s seconds" % (time.time() - start_time))
    
    def node2image(self, filepaths):
        
        # run find_bmu to obtain BMU for each feature vector
        
        bmu_list = []
        for vec in self.data:
            bmu_list.append(self.find_bmu(vec))
        
        # storing the result in a dataframe. 
        # i-th row of the dataframe (ex: 4 1) is associated with the BMU coordinates of the i-th feature vector  
        data_ = pd.DataFrame(bmu_list, columns=['BMU_x','BMU_y'])
        
        # merge the 2 dataframes
        df = pd.concat([filepaths, data_], axis=1, join='inner')

        # now we have:
        
        # filename ID BMU_x BMU_y
        # ........ rows ........
        
        # calling next function to select images 
        return df
        
    def select_images(self, df):
        
        # empty dataframe with column names
        selected_images = pd.DataFrame(columns = ['filename', 'ID', 'BMU_x', 'BMU_y'])
        
        for i in range(self.som_size):
            for j in range(self.som_size):
                
                tmp = df.loc[(df.BMU_x == i) & (df.BMU_y == j)]
                    
                if(len(tmp) != 0):
                        
                    ## random selection (for now) ##
                    sample = tmp.sample()
                    selected_images = selected_images.append(sample)
        
        print("The following images were selected: ")
        display(selected_images)
        
        # calling next function to display images
        return selected_images
    
    def display_images(self, selected_images):
        
        my_dir = "C:/Users/KWP/bachelor_thesis/native-queries/thumbs/"

        fig, ax = plt.subplots(self.som_size, self.som_size, sharex='col', sharey='row', figsize=(320,180))

        for i in range(len(selected_images)):
    
            row = selected_images.iloc[i,:]
            x = row.BMU_x
            y = row.BMU_y
    
            img = Image.open(my_dir + row.filename)
            img = img.resize((320, 180))
            img = np.asarray(img)
    
            ax[x, y].imshow(img)
        
        plt.tight_layout(pad=0.1, w_pad=0.1, h_pad=0.1)
        plt.show()

In [31]:
# training SOM with size 5 x 5
# Goal: 10 x 10

size = 5
som = SOM(som_size=size, data=frame_features, sigma=1, lambda_=1e2, learning_rate=0.7, iterations=5)

In [32]:
som2 = SOM(som_size=size, data=frame_features, sigma=1, lambda_=1e2, learning_rate=0.7, iterations=5,
     query_scores=query_scores[0], auto_var_adjustment=True)

sum of variance over all SOM nodes' original features: 2.0698651271963557
variance of adjusted query scores: 2.0466575622558594


In [19]:
som.train()

Training complete. Time elapsed: 169.97345447540283 seconds


In [33]:
som2.train()

Training complete. Time elapsed: 162.17654514312744 seconds


In [21]:
som.display_results()

The following images were selected: 


filename     ID BMU_x BMU_y
15466  v05542_s00013(f001156-f001214)_g00021_f001198.jpg  15466     0     0
1420   v00513_s00025(f002650-f003025)_g00073_f002949.jpg   1420     0     1
4051   v01475_s00000(f000000-f000207)_g00002_f000179.jpg   4051     0     2
3873   v01414_s00091(f017739-f018155)_g00146_f018041.jpg   3873     0     4
11932  v04277_s00019(f002321-f002485)_g00089_f002475.jpg  11932     1     0
18649  v06686_s00049(f007325-f007657)_g00100_f007612.jpg  18649     1     1
9177   v03329_s00138(f106452-f115704)_g00399_f115450.jpg   9177     1     2
5704   v02099_s00088(f014880-f014972)_g00229_f014880.jpg   5704     1     3
11692  v04185_s00237(f020898-f020939)_g00274_f020925.jpg  11692     2     0
12093  v04339_s00008(f005032-f005877)_g00057_f005700.jpg  12093     2     3
15724  v05619_s00071(f005889-f006171)_g00099_f006053.jpg  15724     2     4
19211  v06874_s00003(f000226-f006523)_g00086_f006083.jpg  19211     3     1
15071  v05388_s00028(f005992-f006099)_g00045_f006000.jpg  15071     3     2
6324   v02335_s00045(f010987-f012848)_g00080_f011358.jpg   6324     3     3
14304  v05114_s00089(f005592-f005646)_g00121_f005625.jpg  14304     3     4
6225   v02297_s00155(f011085-f011319)_g00240_f011125.jpg   6225     4     0
1212   v00418_s00103(f006063-f006115)_g00150_f006083.jpg   1212     4     1
140    v00052_s00030(f005037-f005097)_g00058_f005094.jpg    140     4     2
19529  v06985_s00035(f005477-f005624)_g00085_f005562.jpg  19529     4     3
17441  v06248_s00035(f003914-f004152)_g00067_f004025.jpg  17441     4     4

Time elapsed: 76.40389251708984 seconds


In [20]:
som2.display_results()

The following images were selected: 


filename     ID BMU_x BMU_y
6225   v02297_s00155(f011085-f011319)_g00240_f011125.jpg   6225     0     0
329    v00117_s00006(f000975-f001320)_g00018_f001078.jpg    329     0     2
9254   v03355_s00056(f008775-f008963)_g00174_f008901.jpg   9254     0     3
5267   v01943_s00061(f006243-f006278)_g00122_f006250.jpg   5267     0     4
10975  v03955_s00228(f028384-f028430)_g00502_f028411.jpg  10975     1     0
13237  v04748_s00053(f004318-f004398)_g00089_f004325.jpg  13237     1     1
10489  v03794_s00044(f003780-f003888)_g00057_f003850.jpg  10489     1     3
1094   v00381_s00068(f007234-f007304)_g00093_f007290.jpg   1094     1     4
3488   v01277_s00087(f009630-f009771)_g00163_f009650.jpg   3488     2     0
15071  v05388_s00028(f005992-f006099)_g00045_f006000.jpg  15071     2     1
13020  v04670_s00008(f000374-f000384)_g00010_f000375.jpg  13020     2     3
18081  v06496_s00009(f000688-f000730)_g00010_f000719.jpg  18081     2     4
16241  v05822_s00005(f012069-f013080)_g00338_f012275.jpg  16241     3     0
1254   v00431_s00014(f001532-f001674)_g00020_f001650.jpg   1254     3     1
16894  v06055_s00084(f016935-f017223)_g00140_f017142.jpg  16894     3     2
3199   v01166_s00023(f013143-f013253)_g00045_f013216.jpg   3199     3     3
11590  v04153_s00001(f000010-f001350)_g00033_f001225.jpg  11590     4     0
86     v00035_s00001(f000036-f000134)_g00001_f000089.jpg     86     4     1
12294  v04403_s00105(f009679-f009772)_g00117_f009734.jpg  12294     4     2
3873   v01414_s00091(f017739-f018155)_g00146_f018041.jpg   3873     4     4

Time elapsed: 77.56732439994812 seconds
